In [ ]:
import pandas as pd
import numpy as np 
import glob
import os 

In [ ]:
calendario = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\CICLO 9\CALENDARIO_CICLO\Ciclo_Expandido_com_Datas.xlsx")

calendario['Date'] = pd.to_datetime(calendario['Date'])

# Get today (normalized to midnight)
today = pd.Timestamp("today").normalize()

calendario['NUM_CICLO'] = calendario['Ciclo'].str[-2:].astype(int)

calendario['ANO_CICLO'] = calendario['Ciclo'].str[0:5]

calendario = calendario[calendario['MARCA'] == "BOTICARIO"]

calendario['CICLOMAIS2'] = calendario['ANO_CICLO'].astype(str) + (calendario['NUM_CICLO'].astype(int) + 3).astype(str).str.zfill(2)       #<<< MUDAR O "4" (CICLO ATUAL + 4 PARA ACHAR O CICLO DA SUGESTÃO) EX: C202505 -> C202509
ciclo_mais2 = calendario[calendario['Date'].dt.normalize() == today]['CICLOMAIS2'].iloc[0]

# Filter rows where date matches today
filtered_calendario = calendario[calendario['Ciclo'] == ciclo_mais2][:1]

filtered_calendario['dias_ate_inicio'] = filtered_calendario['INICIO CICLO'].iloc[0] - today

filtered_calendario['dias_ate_inicio'] = filtered_calendario['dias_ate_inicio'].dt.days.astype(int)

filtered_calendario['match'] = 1


In [ ]:
filtered_calendario

In [ ]:
df_similares = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C11\arquivos para geração da sugestão\SIMILARES\PRODUTOS SIMILARES - BOT.xlsx")

df_similares = pd.merge(left=df_similares,right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], how= 'left', left_on = 'CICLO SIMILAR',right_on = 'Ciclo' )

df_similares = df_similares.drop(columns=['Ciclo'])

df_similares = df_similares.rename(columns={'INICIO CICLO':'INICIO CICLO SIMILAR','FIM CICLO':'FIM CICLO SIMILAR','DURAÇÃO':'DURAÇÃO CICLO SIMILAR'})
df_similares.drop_duplicates(inplace=True)

df_similares['MATCH'] = 1

df_similares = df_similares.drop(columns=['INICIO DO CICLO',
       'FIM DO CICLO', 'DURAÇÃO CICLO','INICIO CICLO SIMILAR','FIM CICLO SIMILAR','DURAÇÃO CICLO SIMILAR'])

In [ ]:
df_similares.columns

In [ ]:
df_tabela = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C11\arquivos para geração da sugestão\TABELA DE PEDIDO\Pedidos Semanais Especiais - BOT - 202511.xlsx")

df_tabela = df_tabela[df_tabela['Região'] == 'NNE'] 

df_tabela = df_tabela[(df_tabela['Canal'] != 'Ecomm') | (df_tabela['Canal'] != 'Ecomm | VD') | (df_tabela['Canal'] != 'Ecomm | Loja')] 

df_tabela['Canal'] = np.where((df_tabela['Canal'] == "Loja") | (df_tabela['Canal'] == "Todos") | (df_tabela['Canal'] == "Loja | VD"),"TODOS","VD")

df_tabela = df_tabela[df_tabela['Tipo de promoção'].str.contains('Lançamentos', na=False)]

In [ ]:
df_pdv = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\PDV\PDV_ATT.xlsx")

df_pdv_origi = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BASE DE DADOS LANÇAMENTO\BOT\PDV\PDV_ATT.xlsx")

df_pdv = df_pdv.rename(columns={'DESCRIÇÃO':'DESCRIÇÃO PDV'})

df_pdv = df_pdv.drop(columns=['REGIÃO', 'ESTADO','CIDADE','GESTÃO','MARCA'])

df_pdv['PDV'] = df_pdv['PDV DESC'].str.split("-").str[0].str.strip()

df_pdv['UF'] = np.where(df_pdv['UF'] == 'VDC','BA',df_pdv['UF'])

#ignorando a PDV que ainda não está online
df_pdv = df_pdv[df_pdv['DESCRIÇÃO PDV'] != '23813-COMERCIO-HIB VALENTE']

df_pdv = df_pdv[df_pdv['status'] != "INATIVO"]

df_pdv = df_pdv[df_pdv['status'] != "MATRIZ"]

df_pdv = df_pdv[df_pdv['SUPERVISOR'] != 'Inativa']

df_pdv['MATCH'] = 1

In [ ]:
df_pdv.columns

In [ ]:
df_similares = pd.merge(left=df_similares,right=df_pdv,right_on=['MATCH'],left_on=['MATCH'],how='inner')

df_similares = df_similares.drop_duplicates()

In [ ]:
# Caminho onde estão as subpastas com os arquivos CSV

# Set the path to the folder containing CSV files
folder_path = r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C11\arquivos para geração da sugestão\DRAFT"  # arquivo dos drafts

# Pattern to match all CSV files
csv_files = glob.glob(os.path.join(folder_path, '*.csv'))

# Read and concat all CSVs
df_draft = pd.concat([pd.read_csv(file) for file in csv_files], ignore_index=True)

df_draft['match'] = 1 

df_draft.shape


In [ ]:
df_draft = df_draft.drop(columns=['Categoria'])

In [ ]:
df_draft.columns[7:25]

In [ ]:
# Define as colunas mensais
colunas_mensais = df_draft.columns[7:25]

# Agrupa por PDV e calcula crescimento médio por PDV
def calcular_crescimento(grupo):
    soma_mensal = grupo[colunas_mensais].sum()             # soma por mês
    variacao_mensal = soma_mensal.pct_change().dropna()    # variação percentual mês a mês
    variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

    if len(variacao_mensal) == 0:
        return pd.Series({'CRESCIMENTO': np.nan})

    media = variacao_mensal.mean()
    desvio = variacao_mensal.std()

    limite_sup = media + 2 * desvio
    limite_inf = media - 2 * desvio

    variacoes_filtradas = variacao_mensal[variacao_mensal.between(limite_inf, limite_sup)]
    crescimento = round(variacoes_filtradas.mean(), 4)
    return pd.Series({'CRESCIMENTO': crescimento})

# Aplica a função por PDV
crescimento_por_pdv = df_draft.groupby('PDV').apply(calcular_crescimento)

# Merge do resultado de volta no dataframe original
df_draft = df_draft.merge(crescimento_por_pdv, on='PDV', how='left')


In [ ]:
df_similares['PDV'] = df_similares['PDV'].astype('Int64')

df_final = pd.merge(left=df_similares,right=df_draft,right_on=['PDV', 'SKU'],left_on=['PDV','PRODUTO SIMILAR'],how='left')

In [ ]:
df_venda_diaria = pd.read_excel(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C11\arquivos para geração da sugestão\VENDAS_DIARIAS\FormFiltroConsultaVendaSintetica_22_05_2025_16_26_17.xls")

df_venda_diaria.shape

In [ ]:
df_venda_diaria.columns

In [ ]:
df_venda_diaria['PDV'] = df_venda_diaria['Unidade de Negócio'].str.split("-").str[0].str.strip()

df_venda_diaria['Dia'] = pd.to_datetime(df_venda_diaria['Dia'], format='%d/%m/%Y')

df_venda_diaria = pd.merge(left=df_venda_diaria,right=calendario[['Ciclo','Date']],left_on='Dia',right_on='Date',how='inner')

df_venda_diaria = df_venda_diaria.drop(columns='Date')

df_venda_diaria.shape

In [ ]:
# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
df_venda_diaria = df_venda_diaria.sort_values(by=['Unidade de Negócio', 'Código do Produto', 'Dia'])

# Calcula a quantidade acumulada até o dia para cada grupo
df_venda_diaria['Quantidade Acumulada'] = (
    df_venda_diaria
    .groupby(['Unidade de Negócio', 'Código do Produto'])['Quantidade']
    .cumsum()
)  # acumulado por grupo até a data da linha

df_venda_diaria.shape

In [ ]:
df_venda_diaria = df_venda_diaria.drop_duplicates()

df_venda_agrupado = df_venda_diaria.groupby(['PDV', 'Código do Produto','Ciclo'])['Quantidade Acumulada'].max().reset_index()
df_venda_agrupado

In [ ]:
df_final = pd.merge(left=df_final, right=filtered_calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO','match','dias_ate_inicio']], right_on='match',left_on='MATCH',how='left')
df_final.shape

In [ ]:
#df_final = df_final.drop(columns=['PDV DESC','status','SKU','Descrição','Lançamento','Item analisado','Planograma','Quantidade por caixa'])

In [ ]:
df_final = pd.merge(left=df_final, right=calendario[['Ciclo','INICIO CICLO','FIM CICLO','DURAÇÃO']], right_on='Ciclo',left_on='CICLO SIMILAR',how='left')
df_final.shape

df_final = df_final.drop_duplicates()

In [ ]:

df_venda_agrupado = df_venda_agrupado.rename(columns={'Quantidade Acumulada':'Vendas Ciclo Lançamento'})

In [ ]:
df_final['PRODUTO LANÇAMENTO'] = df_final['PRODUTO LANÇAMENTO'].astype('Int64')

df_venda_agrupado['PDV'] = df_venda_agrupado['PDV'].astype('Int64')

df_final = pd.merge(left=df_final, right = df_venda_agrupado, right_on=['Ciclo','Código do Produto','PDV'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final = df_final.drop_duplicates()

In [ ]:
df_final['PDV'].value_counts().min()

In [ ]:
df_final.columns[29:46]

In [ ]:
# Suponha que os meses estão nas colunas 10 a 26 (17 colunas = 17 meses)
colunas_mensais = df_final.columns[29:46]

# Passo 1: Soma todas as linhas (itens) por mês → resultado: total por mês
soma_mensal = df_final[colunas_mensais].sum()

# Passo 2: Calcula a variação percentual de um mês para o outro
variacao_mensal = soma_mensal.pct_change()
variacao_mensal = variacao_mensal.dropna()

variacao_mensal = variacao_mensal[np.isfinite(variacao_mensal)]

# Passo 3: Calcula a média da variação (ignorando o primeiro NaN)
media_variacao = variacao_mensal[1:].mean()

# Calcula média e desvio padrão
media = variacao_mensal.mean()
desvio = variacao_mensal.std()

# Define limite (ex: 2 desvios padrão)
limite_superior = media + 2 * desvio
limite_inferior = media - 2 * desvio

# Filtra dados dentro do limite
filtro = variacao_mensal.between(limite_inferior, limite_superior)
df_filtrado = variacao_mensal[filtro]
CRESCIMENTO = round(df_filtrado.mean(),4)

df_final['CRESCIMENTO_GERAL'] = CRESCIMENTO

CRESCIMENTO


In [ ]:
df_final = df_final.drop(columns='Ciclo_y')

df_final = df_final.rename(columns={'Ciclo_x': 'Ciclo',	'INICIO CICLO_x': 'INICIO CICLO',	'FIM CICLO_x':'FIM CICLO' ,'DURAÇÃO_x':'DURAÇÃO',
                                    	'INICIO CICLO_y': 'INICIO CICLO SIMILAR' ,	'FIM CICLO_y': 'FIM CICLO SIMILAR','DURAÇÃO_y':'DURAÇÃO CICLO SIMILAR'})

In [ ]:
df_final.columns[40:47]

In [ ]:
VENDA_SIMILAR_6_MESES= df_final.columns[40:47]

df_final['Pico Vendas Similar Ultimos 6 ciclos'] = df_final[VENDA_SIMILAR_6_MESES].max(axis=1)


df_final['MEDIANA DO HISTÓRICO'] = df_final[colunas_mensais].dropna().median(axis=1)

df_final['Vendas Ciclo Lançamento'] = df_final['Vendas Ciclo Lançamento'].fillna(0)

In [ ]:
medi = df_final.groupby(['CANAL'])['MEDIANA DO HISTÓRICO'].max().reset_index()
medi = medi.rename(columns={'MEDIANA DO HISTÓRICO':'med_por_canal'})
medi

In [ ]:
df_final = pd.merge(left=df_final, right=medi,on='CANAL',how='inner')


In [ ]:
df_vdc = pd.read_csv(r"C:\Users\joao.herculano\GRUPO GINSENG\Assistência Suprimentos - 2025\SUPRIMENTOS\BD_LANÇAMENTOS\BOT\BOT - C11\arquivos para geração da sugestão\VENDAS VDC\vendas_vdc22.02.csv")



df_vdc['DATA VENDA'] = pd.to_datetime(df_vdc['DATA VENDA'])

# 'Dia' já está em formato datetime, então renomeamos para 'Data' diretamente
# ou apenas usamos 'Dia' como referência de data

# Ordena o DataFrame para garantir que a cumulativa funcione corretamente
df_venda_diaria = df_venda_diaria.sort_values(by=['Unidade de Negócio', 'Código do Produto', 'Dia'])

# Calcula a quantidade acumulada até o dia para cada grupo
df_vdc['Quantidade Acumulada vdc'] = (
    df_vdc
    .groupby(['PDVDEPARA.Practico', 'Código'])['Soma de Quantidade']
    .cumsum()
)  # acumulado por grupo até a data da linha

In [ ]:
df_vdc = pd.merge(left=df_vdc,right=calendario[['Date','Ciclo']],left_on='DATA VENDA',right_on='Date',how='inner')

df_vdc_agrupado = df_vdc.groupby(['PDVDEPARA.Practico',	'Código','Ciclo'])['Quantidade Acumulada vdc'].max().reset_index()

df_vdc_agrupado = df_vdc_agrupado.rename(columns={'Ciclo':'Ciclo vdc'})


df_vdc_agrupado.head()

In [ ]:
df_final = pd.merge(left=df_final, right = df_vdc_agrupado, right_on=['Ciclo vdc','Código','PDVDEPARA.Practico'],left_on=['CICLO SIMILAR','PRODUTO SIMILAR','PDV'],how='left')

df_final['Quantidade Acumulada vdc'] = df_final['Quantidade Acumulada vdc'].fillna(0)


df_final['Vendas Ciclo Lançamento'] = np.where(df_final['Quantidade Acumulada vdc']>0, df_final['Quantidade Acumulada vdc'], df_final['Vendas Ciclo Lançamento'])

df_final = df_final.drop(columns='Quantidade Acumulada vdc')


df_final = df_final.drop(columns='Ciclo vdc')



In [ ]:
df_final['CRESCIMENTO_FINAL'] = df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'] #crescimento do pdv

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']>0.8,0.8,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

df_final['CRESCIMENTO_FINAL'] = np.where(df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO']<0,0,df_final['CRESCIMENTO_GERAL'] + df_final['CRESCIMENTO'])

df_final['MEDIANA DO HISTÓRICO'] = np.where(df_final['MEDIANA DO HISTÓRICO']==0, df_final['' \
'or_canal'],df_final['MEDIANA DO HISTÓRICO'])

# Primeiro cálculo intermediário
df_final['PV GINSENG'] = np.where(df_final['CRESCIMENTO_FINAL'] * df_final['Vendas Ciclo Lançamento'] + df_final['Vendas Ciclo Lançamento'] < df_final['MEDIANA DO HISTÓRICO'],
                                    round(df_final['CRESCIMENTO_FINAL'] * df_final['MEDIANA DO HISTÓRICO']+ df_final['MEDIANA DO HISTÓRICO'],0), 
                                    round(df_final['CRESCIMENTO_FINAL']*df_final['Vendas Ciclo Lançamento']+df_final['Vendas Ciclo Lançamento'],0))

df_final['PV GINSENG'] = np.where(df_final['PV GINSENG'].isna(),df_final['med_por_canal'] ,df_final['PV GINSENG'])

df_final.shape

In [ ]:
df_final.drop(columns=df_final.columns[29:42],inplace=True)

In [ ]:
df_final.columns

In [ ]:

df_final.drop(columns=['status', 'Classe', 'SKU', 'Subcategoria', 'Lançamento',
       'Desativação','Dias sem venda',
       'Projeção Próximo Ciclo', 'Projeção Próximo Ciclo + 1',
       'Promoção Próximo Ciclo', 'Promoção Próximo Ciclo + 1', 'Estoque Atual',
       'Estoque em Transito', 'Pedido Pendente',
       'Compra inteligente semanal/Sugestão de compra',
       'Compra inteligente Próximo Ciclo',
       'Compra inteligente Próximo Ciclo + 1', 'Item Desativado',
       'Data Prevista Regularização', 'Carteira Bloqueada Para Novos Pedidos',
       'Planograma', 'Quantidade por caixa', 'Preço Sell In', 'Quantidade',
       'Item analisado', 'match_x',
       'CRESCIMENTO', 'Ciclo', 'INICIO CICLO', 'FIM CICLO', 'DURAÇÃO',
       'match_y', 'dias_ate_inicio', 'INICIO CICLO SIMILAR','med_por_canal', 'CRESCIMENTO_FINAL',
       'FIM CICLO SIMILAR', 'DURAÇÃO CICLO SIMILAR', 'Código do Produto','CRESCIMENTO_GERAL'],inplace=True)
df_final.columns

In [ ]:
df_final.columns[23:28]

In [ ]:
df_final = df_final.rename(columns={df_final.columns[23]: "C-4", df_final.columns[24]: "C-3",df_final.columns[25]: "C-2",df_final.columns[26]: "C-1",df_final.columns[27]:'VENDAS CICLO ATUAL'})


In [ ]:
df_final.columns = df_final.columns.str.upper()

df_final.drop(columns=df_final.filter(regex='HISTÓRICO DE VENDAS DO CICLO').columns, inplace=True)

df_final.columns

In [ ]:
df_final = df_final.drop(columns=['DESCRIÇÃO','MEDIANA DO HISTÓRICO'])

In [ ]:
df_final.shape

In [ ]:
df_final = df_final.reindex(columns=[
    'SUPERVISOR',
    'ANALISTA',
    'CANAL',
    'UF',
    'PDV',
    'PDV DESC',
    'PRODUTO LANÇAMENTO',
    'DESCRIÇÃO DO LANÇAMENTO',
    'MARCA',
    'CATEGORIA',
    'MECANICA CONSUMIDOR',
    '% CONSUMIDOR',
    'MECANICA REVENDEDOR',
    '% REVENDEDOR',
    'TIPO DE PRODUTO',
    'IAF',
    'FOCO',
    'SKU',
    'PRODUTO SIMILAR',
    'DESCRIÇÃO SIMILAR',
    'CICLO SIMILAR',
    'VENDAS CICLO LANÇAMENTO',
    'C-4',
    'C-3',
    'C-2',
    'C-1',
    'VENDAS CICLO ATUAL',
    'PICO VENDAS SIMILAR ULTIMOS 6 CICLOS',
    'PV GINSENG'])


In [ ]:
df_final['SUGESTÃO METASELLIN'] = ''
df_final['SUGESTÃO ABASTECIMENTO'] = ''
df_final['SUGESTÃO COMERCIAL'] = ''


In [ ]:
df_final.to_excel(r'C:\Users\joao.herculano\Documents\sugest.xlsx',index=False)